## 2018-08-29
- 크롤링 방식 선정 관련
>- 다음 웹툰의 경우 json 형태로 데이터를 읽어오면 손쉽게 코멘트와 부수정보를 얻을 수 있음.
    - 메인화면
        - 특정 만화 목록 [기다리면무료 json ex)] : http://webtoon.daum.net/data/pc/webtoon/list_gidamoo
        - 특정 만화 목록 [완결 json ex)] : http://webtoon.daum.net/data/pc/webtoon/list_finished/?genre_id=&timeStamp=1535525278698
        - 크롤링 결정 [모바일웹>웹툰>평점순] : http://m.webtoon.daum.net/data/mobile/webtoon?sort=score&page_size=9999&page_no=1
        - 얻을 수 있는 정보 목록 :
            - 만화 목록
            - 만화의 간략정보
    - 만화 정보 및 회차 url : http://webtoon.daum.net/webtoon/view/AnOutcast
        - 만화 정보 및 회차목록 json ex) : http://webtoon.daum.net/data/pc/webtoon/view/AnOutcast?timeStamp=1535525697456
        - 얻을 수 있는 정보 목록 :
            - 장르카테고리 : 확인된건 한번에 5개씩(??)
            - 만화의 전체 회차
            - 글/작가 artist정보
            - 만화의 제목 및 닉네임
            - 평점 score
            - 추천되는 다른 만화의 정보
    - 만화 내용 및 댓글 url : http://webtoon.daum.net/webtoon/viewer/54701
        - 만화 회차 댓글목록 json ex) : http://hestia.webtoon.daum.net/hestia/api/v1/comment/webtoon_ep/54701?page=1&pageSize=99999&sortType=recommend&1535524756659
        - 얻을 수 있는 정보 목록 : 
            - 볼수 있는 만화회차의 댓글전체, 추천/비추천 현황(유료제외)

In [126]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

import numpy as np
import scipy as sp
import pandas as pd
import statsmodels.api as sm
import statsmodels.formula.api as smf
import statsmodels.stats.api as sms
import sklearn as sk

%matplotlib inline
%config InlineBackend.figure_formats = {'png','retina'}

import matplotlib as mpl
import matplotlib.pylab as plt
from mpl_toolkits.mplot3d import Axes3D

import seaborn as sns
sns.set()
sns.set_style("whitegrid")
sns.set_color_codes()

In [1]:
# scrapy

In [4]:
import scrapy
import requests
from scrapy.http import TextResponse

In [5]:
req = requests.get('http://webtoon.daum.net/#sort=free&genre=&tab=finish')
response = TextResponse(req.url, body=req.text, encoding="utf-8")

In [6]:
response.xpath('//*[@id="daumServiceLogo"]')

[<Selector xpath='//*[@id="daumServiceLogo"]' data='<a href="/" id="daumServiceLogo">\n\t\t\t\t\t<'>]

In [7]:
# bs4-json

In [8]:
import pandas as pd
from pandas.io.json import json_normalize

    # url제조함수
def make_url(pageSize=10, page=1):
    return 'http://webtoon.daum.net/data/pc/webtoon/list_finished/?genre_id=&timeStamp=1535525278698'

    # 데이터를 가져와서 판다스의 데이터프레임으로 만드는 함수
def get_data(url):
    response = requests.get(url)
    json_info = response.json() #json -> dict 형식으로 알아서 바꿔줌
    a = json_info
#     companys = json_info["result"]["itemList"] #list 형태로 바꿔줌
#     a = json_normalize(companys)
    
    #행이름 바꾸기
#     a.columns = ["주식수량","거래량","종목코드","등락율","전일비","시가총액","mt","종목","시세","전일가","rf"]

    # 일일이 열에 넣는방법은 아래와 같다    
#     df = pd.DataFrame(columns=["종목","시세","전일비","등락율","시가총액","거래량"])
    
#     for company in companys:
#         df.loc[len(df)] = {
#             "종목":company["nm"],
#             "시세":company["nv"],
#             "전일비":company["cv"],
#             "등락율":company["cr"],
#             "시가총액":company["mks"],
#             "거래량":company["aq"]
#         }
    
    return a
    
    
#---함수를 써보자--------------------------    
url = make_url(5,1)
datas = get_data(url)
datas

{'result': {'status': '200', 'message': ''},
 'data': [{'id': 1518,
   'nickname': 'animalhero',
   'webtoonType': 'series',
   'title': '애니멀 히어로-닥터 슈바이처',
   'finishYn': 'Y',
   'thumbnailImage2': {'id': 0,
    'url': 'http://t1.daumcdn.net/webtoon/op/d1776151dc67c4cba16dd8c94f8c3b61f398f4a9'},
   'pcThumbnailImage': {'id': 0,
    'url': 'http://t1.daumcdn.net/webtoon/op/c49acc62577c282aa55fb3470d3e3824ba7499c7'},
   'finishDate': '20180829000000',
   'ageGrade': 0,
   'dateCreated': '20180730160439',
   'cartoon': {'artists': [{'name': '유쏘', 'penName': '유쏘'},
     {'name': '백준', 'penName': '백준'}]},
   'latestWebtoonEpisode': {'id': 55088,
    'episode': 5,
    'title': '5화 호더(hoarder) - 목욕탕의 여신',
    'thumbnailImage': {'id': 55088,
     'url': 'http://t1.daumcdn.net/webtoon/op/6b4e20e8dd5cc8a7ca4c42368261a4e6ca8e47fb'},
    'encryptUseYn': 'N',
    'serviceStatus': 'service',
    'articleId': 0,
    'dateCreated': '20180828114014',
    'price': 0,
    'isTopRecommend': False,
    'is

In [9]:
datas['data'][0].keys()

dict_keys(['id', 'nickname', 'webtoonType', 'title', 'finishYn', 'thumbnailImage2', 'pcThumbnailImage', 'finishDate', 'ageGrade', 'dateCreated', 'cartoon', 'latestWebtoonEpisode', 'webtoonServices', 'isNew', 'averageScore', 'gidamoo'])

In [10]:
ls_titles = []
ls_nicknames = []
for i in datas['data']:
    ls_titles.append(i['title'])
    ls_nicknames.append(i['nickname'])
ls_titles[:5], ls_nicknames[:5]

(['애니멀 히어로-닥터 슈바이처', '너는 아름답다', '강철강', '골든왈츠', '위 아 애니멀스'],
 ['animalhero', 'yourbeautiful', 'steelsteel', 'GoldenWaltz', 'WeAreAnimals'])

---
# 다음 데이터 크롤링 
### 1. 연재웹툰정보 크롤링
- a) 연재중 웹툰정보 :  http://m.webtoon.daum.net/data/mobile/webtoon?sort=score&page_size=9999&page_no=1
- b) 1부리그 웹툰정보 : http://m.webtoon.daum.net/data/pc/leaguetoon/list?level=major&sort=recommendCnt&page_no=1&page_size=999

In [13]:
# a) 연재중 웹툰정보

url1 = 'http://m.webtoon.daum.net/data/mobile/webtoon?sort=score&page_size=9999&page_no=1'

wbtn_raw1 = get_data(url1)
wbtn_raw1

{'result': {'status': '200', 'message': ''},
 'page': {'size': 9999, 'no': 1, 'groupRange': 4, 'totalItemCount': 765},
 'data': {'isLogin': False,
  'phoneType': None,
  'webtoonTotalCount': 765,
  'webtoons': [{'id': 1531,
    'nickname': 'shootingstar',
    'webtoonType': None,
    'title': '별똥별이 떨어지는 그 곳에서 기다려',
    'englishTitle': None,
    'finishYn': 'N',
    'titleImage2': None,
    'thumbnailImage': None,
    'thumbnailImage2': {'id': 0,
     'url': 'http://t1.daumcdn.net/webtoon/op/2ff712b2024026f143687a46cc757c533174da71',
     'name': None,
     'size': None,
     'width': 0,
     'height': 0,
     'mediaType': None,
     'encryptKey': None,
     'serviceStatus': 'service'},
    'padThumbnailImage': None,
    'artistCommentImage': None,
    'homeThumbnailImage': None,
    'appThumbnailImage': {'id': 0,
     'url': 'http://t1.daumcdn.net/webtoon/op/d571ea54bf60adf2cc896cf9b77ce1f35804818f',
     'name': None,
     'size': None,
     'width': 0,
     'height': 0,
     'mediaTy

In [14]:
wbtn_raw1.keys()

dict_keys(['result', 'page', 'data', 'metaData'])

In [136]:
wbtn_raw1['data']['webtoons'][0].keys()
wbtn_raw1['data']['webtoons'][1]

dict_keys(['id', 'nickname', 'webtoonType', 'title', 'englishTitle', 'finishYn', 'titleImage2', 'thumbnailImage', 'thumbnailImage2', 'padThumbnailImage', 'artistCommentImage', 'homeThumbnailImage', 'appThumbnailImage', 'pcThumbnailImage', 'pcRecommendImage', 'pcHomeImage', 'pcHomeRightImage', 'pcHomeLeftColor', 'pcHomeRightColor', 'introduction', 'startDate', 'finishDate', 'restartDate', 'serviceStatus', 'viewerType', 'weekTerm', 'articleId', 'media', 'url', 'simpleUrl', 'webtoonGroupId', 'payYn', 'payType', 'price', 'ageGrade', 'restYn', 'monopolize', 'dateCreated', 'webtoonComment', 'cartoon', 'cp', 'webtoonWeeks', 'webtoonEpisodes', 'previewWebtoonEpisodes', 'latestWebtoonEpisode', 'webtoonServices', 'relatedProducts', 'promotionContents', 'score', 'tag', 'isNew', 'averageScore', 'seriesYn', 'ranking', 'diff', 'metricsScore', 'eventBanners', 'sort', 'sortWeight', 'gidamoo', 'webtoonNotice', 'couponAvailable'])

{'id': 1444,
 'nickname': 'vacantly',
 'webtoonType': None,
 'title': '우두커니',
 'englishTitle': None,
 'finishYn': 'N',
 'titleImage2': None,
 'thumbnailImage': None,
 'thumbnailImage2': {'id': 0,
  'url': 'http://t1.daumcdn.net/webtoon/op/22a74c4f0490c8883cb1b253ae271ef38df0851a',
  'name': None,
  'size': None,
  'width': 0,
  'height': 0,
  'mediaType': None,
  'encryptKey': None,
  'serviceStatus': 'service'},
 'padThumbnailImage': None,
 'artistCommentImage': None,
 'homeThumbnailImage': None,
 'appThumbnailImage': {'id': 0,
  'url': 'http://t1.daumcdn.net/webtoon/op/937d2b06e473f16a750f176c749473de67735eb1',
  'name': None,
  'size': None,
  'width': 0,
  'height': 0,
  'mediaType': None,
  'encryptKey': None,
  'serviceStatus': 'service'},
 'pcThumbnailImage': None,
 'pcRecommendImage': None,
 'pcHomeImage': None,
 'pcHomeRightImage': None,
 'pcHomeLeftColor': None,
 'pcHomeRightColor': None,
 'introduction': None,
 'startDate': None,
 'finishDate': None,
 'restartDate': None,
 '

In [88]:
wbt1_df = pd.DataFrame(columns = ['id', 'nickname', 'webtoonType', 'title', 'englishTitle', 'finishYn', 'titleImage2', 'thumbnailImage', 'thumbnailImage2', 'padThumbnailImage', 'artistCommentImage', 'homeThumbnailImage', 'appThumbnailImage', 'pcThumbnailImage', 'pcRecommendImage', 'pcHomeImage', 'pcHomeRightImage', 'pcHomeLeftColor', 'pcHomeRightColor', 'introduction', 'startDate', 'finishDate', 'restartDate', 'serviceStatus', 'viewerType', 'weekTerm', 'articleId', 'media', 'url', 'simpleUrl', 'webtoonGroupId', 'payYn', 'payType', 'price', 'ageGrade', 'restYn', 'monopolize', 'dateCreated', 'webtoonComment', 'cartoon', 'cp', 'webtoonWeeks', 'webtoonEpisodes', 'previewWebtoonEpisodes', 'latestWebtoonEpisode', 'webtoonServices', 'relatedProducts', 'promotionContents', 'score', 'tag', 'isNew', 'averageScore', 'seriesYn', 'ranking', 'diff', 'metricsScore', 'eventBanners', 'sort', 'sortWeight', 'gidamoo', 'webtoonNotice', 'couponAvailable'])

for data in wbtn_raw1['data']['webtoons']:
    wbt1_df.loc[len(wbt1_df)] = data
    
wbt1_df.tail(20)

id        nickname webtoonType        title        englishTitle  \
745   185             MIC        None          MIC                 MIC   
746  1294    FourDeathCut        None  사컷 : 죽음의 소리                None   
747    92             enm        None          눈코입                None   
748   902           baram        None      바람을 가르며                None   
749  1035             mia        None           미아                None   
750   803      Guardians2        None        가디언스2          Guardians2   
751   591          mr_kim        None    신입사원 김이병씨                None   
752   931              3m        None           3M                  3M   
753   784         pandasi        None    아침에 시 한 수                None   
754   871         psychic        None         별호도감                None   
755   177          xianon        None           샤논              Xianon   
756   713     thanksandok        None     고마워 다행이야                None   
757   166       mythology        None         신화전설           mythology   
758   525      st_fighter        None         스트리트      Street Fighter   
759  1172         asphalt        None      아스팔트 정원                None   
760  1036          ramyun        None         군대라면                None   
761   622       Freestyle        None     프리스타일 풋볼  Freestyle Football   
762  1182      deathsight        None       죽음이 본다                None   
763   777  guanghaistory2        None       광해이야기2                None   
764  1222          gochoo        None   여기 고수 추가요!                None   

    finishYn titleImage2 thumbnailImage  \
745        Y        None           None   
746        Y        None           None   
747        Y        None           None   
748        Y        None           None   
749        Y        None           None   
750        Y        None           None   
751        Y        None           None   
752        Y        None           None   
753        Y        None           None   
754        Y        None           None   
755        Y        None           None   
756        Y        None           None   
757        Y        None           None   
758        Y        None           None   
759        Y        None           None   
760        Y        None           None   
761        Y        None           None   
762        Y        None           None   
763        Y        None           None   
764        Y        None           None   

                                       thumbnailImage2  \
745  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
746  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
747  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
748  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
749  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
750  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
751  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
752  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
753  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
754  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
755  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
756  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
757  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
758  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
759  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
760  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
761  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
762  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
763  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   
764  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...   

                                     padThumbnailImage       ...        \
745  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...       ...         
746  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...       ...         
747  {'id': 0, 'url': 'http://i1.cartoon.daumcdn.ne...       ...         
748  {'id': 0, 'url': 'http://i1.

In [137]:
# NaN,None값으로만 이루어진 column 제거
nulldf = wbt1_df.isnull().sum()==765
# nulldf[nulldf==False].keys() 
wbt1_df2 = wbt1_df[['id', 'nickname', 'title', 'englishTitle', 'finishYn', #'viewerType',
       'thumbnailImage2', #'appThumbnailImage', 'padThumbnailImage',
        #'articleId', 'price',
        'ageGrade', 'restYn', 'dateCreated',
       'cartoon', 'latestWebtoonEpisode', 'webtoonServices', 'isNew',
       'averageScore',# 'ranking', 'diff', 'metricsScore', 'sortWeight',
       #'gidamoo', 'couponAvailable'
        ]]
wbt1_df2.columns

Index(['id', 'nickname', 'title', 'englishTitle', 'finishYn',
       'thumbnailImage2', 'ageGrade', 'restYn', 'dateCreated', 'cartoon',
       'latestWebtoonEpisode', 'webtoonServices', 'isNew', 'averageScore'],
      dtype='object')

In [142]:
# 썸네일 이미지 링크 정제
new_temp = pd.DataFrame(columns=['url'])
for data in wbt1_df2['thumbnailImage2']:
    new_temp.loc[len(new_temp)] = data['url']
new_temp.tail()

url
0    http://t1.daumcdn.net/webtoon/op/2ff712b202402...
1    http://t1.daumcdn.net/webtoon/op/22a74c4f0490c...
2    http://t1.daumcdn.net/webtoon/op/c3253c40fad2b...
3    http://t1.daumcdn.net/webtoon/op/7e928b34b6881...
4     http://t1.daumcdn.net/cartoon/59226D8606616F0002
5     http://t1.daumcdn.net/cartoon/589C270E0613690002
6    http://t1.daumcdn.net/webtoon/op/a5224500a171c...
7    http://t1.daumcdn.net/webtoon/op/a2b104a6c2bdf...
8    http://t1.daumcdn.net/webtoon/op/0977e22c24456...
9    http://t1.daumcdn.net/webtoon/op/0cec6619c01b9...
10   http://t1.daumcdn.net/webtoon/op/6d9218f2cde43...
11   http://t1.daumcdn.net/webtoon/op/f4677e5c55d3d...
12   http://t1.daumcdn.net/webtoon/op/0ca4805183bfa...
13   http://t1.daumcdn.net/webtoon/op/b2929cc109dbf...
14   http://t1.daumcdn.net/webtoon/op/e54339607658c...
15   http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
16   http://t1.daumcdn.net/webtoon/op/c057a40175c11...
17   http://t1.daumcdn.net/webtoon/op/dd62fef1540ee...
18   http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
19   http://t1.daumcdn.net/webtoon/op/db4a8113772f6...
20   http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
21   http://t1.daumcdn.net/webtoon/op/b4527691cdec3...
22   http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
23    http://t1.daumcdn.net/cartoon/58F0326B023E740001
24    http://t1.daumcdn.net/cartoon/58E5FB15025D5F0001
25    http://t1.daumcdn.net/cartoon/58D4C67F0509370001
26   http://t1.daumcdn.net/webtoon/op/e2a65561cc4c3...
27    http://t1.daumcdn.net/cartoon/589BCE330221E50001
28   http://t1.daumcdn.net/webtoon/op/319d46d4def73...
29   http://t1.daumcdn.net/webtoon/op/6c17c1f78082d...
..                                                 ...
735  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
736  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
737  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
738  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
739  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
740  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
741  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
742  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
743  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
744  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
745  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
746  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
747  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
748  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
749  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
750  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
751  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
752  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
753  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
754  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
755  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
756  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
757  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
758  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
759  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
760  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
761  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
762  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
763  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...
764  http://i1.cartoon.daumcdn.net/svc/image/U03/ca...

[765 rows x 1 columns]

In [159]:
# 글/그림 작가 모으기
new_temp2 = pd.DataFrame(columns=['artist_name'])
# wbt1_df2['cartoon'][3]['artists']
for data in wbt1_df2['cartoon']:
    new_temp2.loc[len(new_temp2)] = data['artists'][0]['name']+'/'+data['artists'][1]['name']
new_temp2

artist_name
0                      만물상/만물상
1                      심우도/심우도
2                      이은재/이은재
3                       지민/Hun
4                        광진/광진
5                        기기/기기
6                      배혜수/배혜수
7                        보리/보리
8                  bodam/bodam
9                        무류/무류
10                     이현석/노경찬
11                       구리/구리
12                       복슬/복슬
13                     고선영/고선영
14                     박흥용/박흥용
15                       서결/서결
16                     강형규/강형규
17                   인토르노/인토르노
18                     박혜림/박혜림
19                      김종욱/이림
20                       장이/장이
21                       도약/요신
22                       보리/보리
23                       우현/우현
24                     이이영/이이영
25                       강풀/강풀
26                     정종수/정종수
27                     윤태호/윤태호
28                     김나임/김나임
29                       기비/기비
..                         ...
735                    조경규/조경규
736                yami /yami 
737                yami /yami 
738                      임준/임준
739                      와자/와자
740                    최인환/최인환
741                      알콘/알콘
742                      마진/마진
743                    박상선/박상선
744  DAUM WEBTOON/DAUM WEBTOON
745                  2top/2top
746                    유난희/최승범
747                      와자/와자
748                   이강산/커피내음
749                  INJO/INJO
750        ZERO BASE/ZERO BASE
751                    김상수/김상수
752                    강도하/강도하
753                    조경규/조경규
754            불타는 오렌지/불타는 오렌지
755                      알콘/알콘
756                    장대현/장대현
757                  해민유철/해민유철
758          V.A (SF)/V.A (SF)
759                    이원진/이원진
760                    김병관/김병관
761                      임준/임준
762                  INJO/INJO
763  DAUM WEBTOON/DAUM WEBTOON
764                      흑석/흑석

[765 rows x 1 columns]

In [190]:
# 마지막 업로드 일자/ 현재(완료) 회차
new_temp3 = pd.DataFrame(columns=['count_chapter'])
new_temp4 = pd.DataFrame(columns=['latest_Created'])
for data in wbt1_df2['latestWebtoonEpisode']:
    try:
        new_temp3.loc[len(new_temp3)]= data['episode']
    except:
        new_temp3.loc[len(new_temp3)]= None
    try:
        new_temp4.loc[len(new_temp4)]= data['dateCreated']
    except:
        new_temp4.loc[len(new_temp4)]= None
         
new_temp3
new_temp4

count_chapter
0               1
1              19
2               1
3              26
4              83
5              62
6              96
7               1
8              30
9              24
10             44
11             17
12             44
13              1
14             17
15             93
16             11
17             32
18             95
19             19
20            228
21              3
22             14
23             42
24             49
25             46
26             36
27              7
28             33
29             16
..            ...
735             3
736            28
737           158
738            20
739            28
740            53
741            13
742            36
743            63
744             3
745             9
746           135
747            35
748            15
749            24
750            33
751            25
752             3
753            62
754            30
755            22
756            14
757            26
758             6
759            39
760            25
761            10
762            22
763             4
764            26

[765 rows x 1 columns]

latest_Created
0    20180825000000
1    20180731000100
2    20180826000000
3    20170110000200
4    20180703000000
5    20180826000100
6    20180829000100
7    20180826000000
8    20180829000100
9    20180628000000
10   20180828000100
11   20180830000100
12   20180829000100
13   20180828000000
14   20180829000100
15   20180825000100
16   20180207000000
17   20180824000100
18   20180513000000
19   20180829000100
20   20170928000000
21   20180323102902
22   20151011000100
23   20180226000000
24   20180316000000
25   20180101000000
26   20180830000100
27   20170223000200
28   20180713000000
29   20180829000100
..              ...
735  20100823092507
736  20140401090651
737  20121030100710
738  20110109101051
739  20110113130426
740  20161014000100
741  20120820100026
742  20091228001549
743  20131009122147
744  20100731152354
745  20100509085227
746  20180304000100
747  20090825084541
748  20130212094334
749  20140502090908
750  20120630120340
751  20101222094448
752  20130215003031
753  20111212113004
754  20121229085101
755  20100815140557
756  20110724094300
757  20100505104620
758  20100714135215
759  20150923101549
760  20140218085559
761  20110114090438
762  20150628000100
763  20110913083459
764  20151225000100

[765 rows x 1 columns]

In [198]:
df = wbt1_df2[['id', 'nickname', 'title', 'finishYn', #'englishTitle',
       'ageGrade', 'restYn', 'dateCreated', 'isNew', 'averageScore']]
df['artist']=new_temp2
df['latest_upload']=new_temp4
df['last_chapter']=new_temp3
df['img_url']=new_temp
df

C:\Users\creal\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\creal\Anaconda3\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  after removing the cwd from sys.path.
C:\Users\creal\Anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] 

id        nickname                title finishYn ageGrade restYn  \
0    1531    shootingstar  별똥별이 떨어지는 그 곳에서 기다려        N        0      N   
1    1444        vacantly                 우두커니        N        0      Y   
2    1530           i_run               나는 달린다        N        0      N   
3    1313   LikeButterfly                 나빌레라        Y        0      N   
4    1338    ItaewonClass              이태원 클라쓰        Y        0      N   
5    1346       hellobree                헬로 브리        N        0      N   
6    1299           pocha                 쌍갑포차        N        0      N   
7    1532    nightperfume                 밤의 향        N       19      N   
8    1421    rooftopbread                  옥탑빵        N        0      N   
9    1415        findjuly           어쩌다 발견한 7월        A        0      Y   
10   1395       Matchless                 아비무쌍        N        0      N   
11   1467    guricomeback          구리의 구리구리 컴백        N        0      N   
12   1386     KimTeachers            우리학교 김선생님        N        0      N   
13   1533  hellomyandroid          헬로 마이 안드로이드        N        0      N   
14   1466       dawnwings                 새벽날개        N        0      N   
15   1314      BeforeWarm           발자국이 녹기 전에        N        0      N   
16   1400   originalscene               오리지널 씬        Y        0      N   
17   1407       nodesires           작약만가 : 불환곡        N        0      N   
18   1271        doggaebi                도깨비훈장        Y        0      Y   
19   1460     homeofelder                노인의 집        N        0      N   
20     40         perfect               퍼펙트 게임        Y        0      N   
21   1440    makeupartist                  매분구        Y        0      N   
22   1225    destiny_line                    실        Y        0      N   
23   1358      SecondHome                두번째 집        Y        0      N   
24   1356          Garang                 가랑가랑        Y        0      N   
25   1355          bridge                  브릿지        Y        0      N   
26   1410   herosvariable               영웅의 변수        N        0      N   
27   1344       operation               인천상륙작전        Y        0      N   
28   1405    princessbari                 바리공주        N        0      Y   
29   1468         loveway          우리가 사랑하는 방법        N        0      N   
..    ...             ...                  ...      ...      ...    ...   
735   552   panda_chabong           팬더댄스와 차봉클럽        Y        0      N   
736  1009          gongee            공긔 엇더하니잇고        Y        0      N   
737   187           koala                 코알랄라        Y        0      N   
738   561    anywayoffice             얼렁뚱땅 사무소        Y        0      N   
739   589        ambrosia                암브로시아        Y        0      N   
740  1231    AsianHighway             아시안 하이웨이        Y        0      N   
741   864   missingforest                미궁의 숲        Y        0      N   
742    87             fss                환상스케치        Y        0      N   
743   873         gangnam                   강남        Y        0      N   
744   532   guanghaistory                광해이야기        Y        0      N   
745   185             MIC                  MIC        Y        0      N   
746  1294    FourDeathCut          사컷 : 죽음의 소리        Y       19      Y   
747    92             enm                  눈코입        Y        0      N   
748   902           baram              바람을 가르며        Y        0      N   
749  1035             mia                   미아        Y        0      N   
750   803      Guardians2                가디언스2        Y        0      N   
751   591          mr_kim            신입사원 김이병씨        Y        0      N   
752   931              3m                   3M        Y        0      N   
753   784         pandasi            아침에 시 한 수        Y        0      N   
754   871         psychic                 별호도감        Y        0      N   
755   177          xianon                   샤논        Y        0      N   
756   713     thanksandok       